This notebook contain RSW and NTW residual comparisons

## Initialize

In [1]:
run_list = [  'msis2'       ,
             'tiegcm_oc'   ,
            'dtm2020_o'   ,
             'jb2008'      ,
#               'hasdm_oc'    ,
              'ctipe_oc'    ,
           ]




run_dict={}
for i in run_list:
    if i =='msis2':
        num = 5
#         cd= 1.236791
    if i =='tiegcm_oc':
        num = 0
#         cd =  1.372949
    if i =='dtm2020_o':
        num = 3
#         cd = 3.351462
    if i =='jb2008':
        num = 1
#         cd =  1.908777
    if i =='hasdm_oc':
        num = 2
#         cd = 2.076144
    if i =='ctipe_oc':
        num = 4 
#         cd = 4.368334
        
        
    run_dict[i]= (num) #cd

print(run_dict)


{'msis2': 5, 'tiegcm_oc': 0, 'dtm2020_o': 3, 'jb2008': 1, 'ctipe_oc': 4}


In [2]:
# %load_ext autoreload
# %autoreload 2

# import sys  
# import pickle 
# import gc

# sys.path.insert(0, '/data/geodyn_proj/pygeodyn/pygeodyn_develop/')
# from PYGEODYN import Pygeodyn

# for i,val in enumerate(run_list):   
#     run_settings = '/data/zach_work/Paper2022_assessment/runsettings/2week_'+val+'.yaml'
#     ### Load the data into an object
#     RunObject = Pygeodyn(run_settings)
#     RunObject.RUN_GEODYN()
#     RunObject = 0
#     gc.collect()
            
# sys.exit()

###  Input/Read GEODYN Runs and dump to pickle, or load the pickle

#### Two week

In [3]:
# for i,val in enumerate(run_list): 
#     for ii in ['']:
# EDIT_OBJECT_DATES = 0
%load_ext autoreload
%autoreload 2

import sys  
import pickle 
import gc
import os

sys.path.insert(0, '/data/geodyn_proj/pygeodyn/pygeodyn_develop/')
from PYGEODYN import Pygeodyn
 
dir_save = '/data/data_geodyn/results/icesat2/Paper2022_assessment/TwoWeekOutputs/'
for i,val in enumerate(run_list):   
    
    if val == 'hasdm_oc':
#         pickle_file = dir_save+'RSW_2week_valid_'+val+'_gaps.pkl'
        pickle_file = dir_save+'2week_valid_'+val+'_gaps.pkl'
        print('CORRECT:',pickle_file)

    else:
#         pickle_file = dir_save+'RSW_2week_valid_'+val+'.pkl'
        pickle_file = dir_save+'2week_valid_'+val+'.pkl'

    if not os.path.exists(pickle_file):

        print('Must create pickle file...')
        print('   ',  pickle_file)
        print('   ', 'Reading Geodyn Data')
        
        
        run_settings = '/data/zach_work/Paper2022_assessment/runsettings/2week_'+val+'.yaml'
        ### Load the data into an object
        Obj_accels = Pygeodyn(run_settings)
        Obj_accels.getData_BigData_lowmemory()
        gc.collect()

        #### Pickle the object to save it
        print('   ', 'Saving pickle')
        filehandler = open(pickle_file, 'wb') 
        pickle.dump(Obj_accels, filehandler)
        filehandler.close()
        Obj_accels = 0
        print('   ', 'Saved pickle')


    else:
        print(val,i,'  Pickle created -- will load in next step', sep='')
Obj_2weeks = {}

for i,val in enumerate(run_list):   
    ### Load the data if the pickles exist
    print()
    print()
    gc.collect()

    dir_save = '/data/data_geodyn/results/icesat2/Paper2022_assessment/TwoWeekOutputs/'
    
    if val == 'hasdm_oc':
#         pickle_file = dir_save+'RSW_2week_valid_'+val+'_gaps.pkl'
        pickle_file = dir_save+'2week_valid_'+val+'_gaps.pkl'
    else:
#         pickle_file = dir_save+'RSW_2week_valid_'+val+'.pkl'
        pickle_file = dir_save+'2week_valid_'+val+'.pkl'
    
    filehandler = open(pickle_file, 'rb') 
    Obj_2weeks[val] = pickle.load(filehandler)
    filehandler.close()
    print('Loaded data from pickle... ', val)


gc.collect()




msis20  Pickle created -- will load in next step
tiegcm_oc1  Pickle created -- will load in next step
dtm2020_o2  Pickle created -- will load in next step
jb20083  Pickle created -- will load in next step
ctipe_oc4  Pickle created -- will load in next step


Loaded data from pickle...  msis2


Loaded data from pickle...  tiegcm_oc


Loaded data from pickle...  dtm2020_o


Loaded data from pickle...  jb2008


Loaded data from pickle...  ctipe_oc


0

### Plot Settings and Features

In [4]:
plots_dir = '/data/zach_work/validation/ICESat2_3month_Validation/final_plots/'

In [5]:
import plotly.graph_objects as go
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import plotly.express as px
import plotly.io as pio   ### Allows you to save plotly figs


import pandas as pd
import datetime
import numpy as np

config = dict({
                'displayModeBar': False,
                'responsive': False,
                'staticPlot': False,
                'displaylogo': False,
                'showTips': False,
                })



import numpy as np
import pandas as pd
import os

# px.colors.colorscale_to_colors()
# plotly.colors.PLOTLY_SCALES["Viridis"]

def get_color(colorscale_name, loc):
    from _plotly_utils.basevalidators import ColorscaleValidator
    # first parameter: Name of the property being validated
    # second parameter: a string, doesn't really matter in our use case
    cv = ColorscaleValidator("colorscale", "")
    # colorscale will be a list of lists: [[loc1, "rgb1"], [loc2, "rgb2"], ...] 
    colorscale = cv.validate_coerce(colorscale_name)
    
    if hasattr(loc, "__iter__"):
        return [get_continuous_color(colorscale, x) for x in loc]
    return get_continuous_color(colorscale, loc)
        

# Identical to Adam's answer
import plotly.colors
from PIL import ImageColor
def get_continuous_color(colorscale, intermed):
    """
    Plotly continuous colorscales assign colors to the range [0, 1]. This function computes the intermediate
    color for any value in that range.

    Plotly doesn't make the colorscales directly accessible in a common format.
    Some are ready to use:
    
        colorscale = plotly.colors.PLOTLY_SCALES["Greens"]

    Others are just swatches that need to be constructed into a colorscale:

        viridis_colors, scale = plotly.colors.convert_colors_to_same_type(plotly.colors.sequential.Viridis)
        colorscale = plotly.colors.make_colorscale(viridis_colors, scale=scale)

    :param colorscale: A plotly continuous colorscale defined with RGB string colors.
    :param intermed: value in the range [0, 1]
    :return: color in rgb string format
    :rtype: str
    """
    if len(colorscale) < 1:
        raise ValueError("colorscale must have at least one color")

    hex_to_rgb = lambda c: "rgb" + str(ImageColor.getcolor(c, "RGB"))

    if intermed <= 0 or len(colorscale) == 1:
        c = colorscale[0][1]
        return c if c[0] != "#" else hex_to_rgb(c)
    if intermed >= 1:
        c = colorscale[-1][1]
        return c if c[0] != "#" else hex_to_rgb(c)

    for cutoff, color in colorscale:
        if intermed > cutoff:
            low_cutoff, low_color = cutoff, color
        else:
            high_cutoff, high_color = cutoff, color
            break

    if (low_color[0] == "#") or (high_color[0] == "#"):
        # some color scale names (such as cividis) returns:
        # [[loc1, "hex1"], [loc2, "hex2"], ...]
        low_color = hex_to_rgb(low_color)
        high_color = hex_to_rgb(high_color)

    return plotly.colors.find_intermediate_color(
        lowcolor=low_color,
        highcolor=high_color,
        intermed=((intermed - low_cutoff) / (high_cutoff - low_cutoff)),
        colortype="rgb",
    )




cols = get_color("Viridis", np.linspace(0, 1, 5))
map_cols = np.linspace(0, 1, 5)
colorscale=[]
for i,val in enumerate(map_cols):
    colorscale.append([val, cols[i]])
    



# Simplify Plotting Schemes:
col1 =  px.colors.qualitative.Plotly[2]
col2 =  px.colors.qualitative.Plotly[4]
col3 =  px.colors.qualitative.Plotly[1]
col4 =  px.colors.qualitative.Plotly[3]
col5 =  px.colors.qualitative.Plotly[4]
col6 =  px.colors.qualitative.Plotly[5]



# Simplify Plotting Schemes:
col_msis2     =  "#2ca02c"
col_jb2008    =  "#ff7f0e"
col_dtm2020   =  "#d62728"
col_tiegcm_oc =  "#17becf"
col_hasdm_oc  =  "#1f77b4"
col_ctipe_oc  =  "#9467bd"
# col_msis2 =  px.colors.qualitative.Plotly[2]
# col_jb2008 =  px.colors.qualitative.Plotly[4]
# col_dtm2020 =  px.colors.qualitative.Plotly[1]
# col_tiegcm_oc =  px.colors.qualitative.Plotly[5]
# col_hasdm_oc =  px.colors.qualitative.Plotly[0]
# col_ctipe_oc =  px.colors.qualitative.Plotly[7]

x_annot_val = 1.1



def get_plot_params(plot_num, model_name_string):
    '''
    INPUT:   
        Plot number, model_name string, x_annot_val
    
    RETURN:
        col, x_annot, y_annot1, y_annot2, m_size,   
    '''
    
    
    if plot_num == 0:
        col = col1
        x_annot = x_annot_val
        y_annot1 = 1
        y_annot2 = .9
        m_size = 3.5
    elif plot_num == 1:
        x_annot = x_annot_val
        y_annot1 = .8
        y_annot2 = .8
        col = col2
        m_size = 3.5
    elif plot_num == 2:
        x_annot = x_annot_val
        y_annot1 = .5
        y_annot2 = .7
        col = col3
        m_size = 3.5
    elif plot_num == 3:
        x_annot = x_annot_val
        y_annot1 = .2
        y_annot2 = .55
        col = col4
        m_size = 3.5
    elif plot_num == 4:
        x_annot = x_annot_val
        y_annot1 =  0 
        y_annot2 = .45
        col = col5
        m_size = 3.5
        
    elif plot_num == 5:
        x_annot = x_annot_val
        y_annot1 =  0 
        y_annot2 = .35
        col = col6
        m_size = 3.5
        
    if model_name_string == 'msis2':
        col=col_msis2
    elif model_name_string == 'dtm2020_o':
        col=col_dtm2020
    elif model_name_string == 'jb2008':
        col=col_jb2008
    elif model_name_string == 'tiegcm_oc':
        col=col_tiegcm_oc
    elif model_name_string == 'hasdm_oc':
        col=col_hasdm_oc
    elif model_name_string == 'ctipe_oc':
        col=col_ctipe_oc
        
    ### Old Models
    elif model_name_string == 'dtm87':
        col='grey'
    elif model_name_string == 'jaachia71':
        col='grey'
    elif model_name_string == 'msis86':
        col='grey'
    elif model_name_string == 'msis00':
        col='tan'
        
    return(col)
        

### Load GPI data

In [6]:
from netCDF4 import Dataset
def read_nc_file( filename, variables):
    ''' This function reads the TIEGCM .nc files and saves the given input variables to a dictionary.
        The breakloop feature is here so that if the file doesn't exist the code can still continue.  '''
    status = os.path.exists(filename)
    
    if status == True:
        data = {}
        for i, var_names in enumerate(variables):
            ncid =  Dataset(filename,"r+", format="NETCDF4")# filename must be a string
            varData = ncid.variables
            data[var_names] = np.array(varData[var_names])  
    elif status == False:
        print('No File Found', filename )
        breakloop = True
        data = 0
        return( data , breakloop)
    breakloop = False
    return(data,breakloop )


arc_list = []

arc_list_18 = np.arange(292,366)
for i in arc_list_18:
    val = '2018'+str(i)
    arc_list.append(int(val))
    
    #     print(val)
    
arc_list_19 = np.arange(1,10)
for i in arc_list_19:
    val = '201900'+str(i)
    arc_list.append(int(val))


path_to_f107 = '/data/data_geodyn/gpi_1960001-2021243_f107aDaily.nc'
variables = ['year_day', 'f107d', 'f107a', 'kp']
f107_data = read_nc_file(path_to_f107, variables)

date = []
kp_list = []
f107d_list = []
f107a_list  = []
date_3hr = []
doy_list    = []



for i,val in enumerate(arc_list):
    
    index = f107_data[0]['year_day']==val
    kp_list.append(f107_data[0]['kp'][index][0])
    f107d_list.append(f107_data[0]['f107d'][index][0])
    f107a_list.append(f107_data[0]['f107a'][index][0])
    doy_list.append(str(f107_data[0]['year_day'][index][0])[-3:])

    date.append(pd.to_datetime( str(val), format='%Y%j'))

    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=0))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=3))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=6))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=9))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=12))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=15))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=18))
    date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=21))
#     date_3hr.append(pd.to_datetime( str(val), format='%Y%j') +pd.Timedelta(hours=24))
    
kp_expand = []
for i in kp_list:
    for ii in i:
        kp_expand.append(ii)
        
        
        
solar_fluxes = {}
solar_fluxes['f107d_list'] = f107d_list
solar_fluxes['f107a_list'] = f107a_list
solar_fluxes['date']       = date
solar_fluxes['date_3hr']   = date_3hr
solar_fluxes['kp_expand']  = kp_expand

f107d_earth = []
f107a_earth = []
######################################################################### 
##### Account for the F10.7 at earth (instead of referenced at 1AU) #####
######################################################################### 

for i_doy,val_doy in enumerate(doy_list):
    iday = int(val_doy)
    theta0 = 2 * np.pi * (iday)/365.
    sfeps = 1.000110 + 0.034221*np.cos(theta0)+0.001280* np.sin(theta0) +0.000719*np.cos(2.*theta0)+0.000077*np.sin(2.*theta0)

    f107d_earth.append(sfeps * solar_fluxes['f107d_list'][i_doy])
    f107a_earth.append(sfeps * solar_fluxes['f107a_list'][i_doy])

solar_fluxes['f107d_earth'] = f107d_earth
solar_fluxes['f107a_earth'] = f107a_earth



### Prepare RMS total Plot arrays

arc_listlist=[  #['2018.292', '2018.293', '2018.294', '2018.295', '2018.296', 
                 #'2018.297', '2018.298', '2018.299' ],                  
                #
                #['2018.304', '2018.305', '2018.306', '2018.307', '2018.308' ],  
                #
                ['2018.313', '2018.314', '2018.315', '2018.316', '2018.317',
                 '2018.318', '2018.319', '2018.320', '2018.321', '2018.322',
                 '2018.323', '2018.324', '2018.325', '2018.326', '2018.327' ],  
                #
                #['2018.335', '2018.336', '2018.337' ],  
                #
                #['2018.349', '2018.350', '2018.351', '2018.352' ],  
                #
                #['2018.356', '2018.357', '2018.358' ],  
                #
               # ['2018.365', '2019.001', '2019.002', '2019.003', '2019.004', 
                # '2019.005', '2019.006', '2019.007', '2019.008',
                #'2019.009'],  
                ]


# Plot Two Weeks  

## NTW 

In [19]:
Obj_2weeks['msis2'].__dict__['OrbitResids']['2018.314.01']

{'data_orbfil': {'Date': 0     2018-11-10 00:03:00
  1     2018-11-10 00:05:00
  2     2018-11-10 00:07:00
  3     2018-11-10 00:09:00
  4     2018-11-10 00:11:00
                ...        
  713   2018-11-10 23:49:00
  714   2018-11-10 23:51:00
  715   2018-11-10 23:53:00
  716   2018-11-10 23:55:00
  717   2018-11-10 23:57:00
  Name: Date_pd, Length: 718, dtype: datetime64[ns],
  'N': [6851897.506712627,
   6853067.641087851,
   6854392.668177032,
   6855825.800020007,
   6857318.948287311,
   6858825.6552378675,
   6860301.937993422,
   6861709.113725655,
   6863015.315548235,
   6864196.091712154,
   6865235.152151081,
   6866123.8460224895,
   6866860.749187686,
   6867451.728653973,
   6867908.130126723,
   6868244.214262269,
   6868475.877144165,
   6868618.9889044585,
   6868686.8460546825,
   6868689.843705116,
   6868634.838882035,
   6868523.673206164,
   6868353.568068823,
   6868116.887549527,
   6867801.212179118,
   6867392.02791895,
   6866874.576643031,
   6866235.223

In [23]:
%load_ext autoreload
%autoreload 2

# yaxis1_range = [-0.23888888888888893, 4.538888888888889] #full_fig.layout.yaxis1.range
# yaxis2_range = [-13.7,  -12.6]# -12.882954062508686] #full_fig.layout.yaxis2.range
# yaxis3_range = [-100, 60] #full_fig.layout.yaxis3.range
# yaxis4_range = [-2, 43] #full_fig.layout.yaxis4.range

def plot_NTWresids(fig, obj_m1, plot_num, solar_fluxes,    arc_listlist ):
    

    ####  Get plot Parameters for this model
    model_m1 = obj_m1.__dict__['global_params']['den_model']
    col = get_plot_params(plot_num, model_m1)
    

    for i1,arc1 in enumerate(arc_listlist):#obj_m1.__dict__['global_params']['arc_input']):
        dateplot = []
        rms_totals = []
        
        for ii,arc in enumerate(arc1):#obj_m1.__dict__['global_params']['arc_input']):
            if arc not in obj_m1.__dict__['global_params']['arc_input']:
                continue
            else:
                arc =arc+'.01'


                ### -----------------------------------------------------------------------------------------------------
                ###     Normal Residuals
                data_resids = obj_m1.__dict__['OrbitResids'][arc]['data_orbfil']
                fig.add_trace(go.Scattergl(x=data_resids['Date'][::75],
                                           y=data_resids['N'][::75],
                                             name= 'Normal',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=1),
                                             showlegend=False),
                                             secondary_y=False, row=1, col=1)
                ### -----------------------------------------------------------------------------------------------------
                ###     In Track Residuals
                data_resids = obj_m1.__dict__['OrbitResids'][arc]['data_orbfil']
                fig.add_trace(go.Scattergl(x=data_resids['Date'][::75],
                                           y=data_resids['T'][::75],
                                             name= 'In track',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=2),
                                             showlegend=False),
                                             secondary_y=False, row=2, col=1)
                ### -----------------------------------------------------------------------------------------------------
                ###     Cross Track Residuals
                data_resids = obj_m1.__dict__['OrbitResids'][arc]['data_orbfil']
                fig.add_trace(go.Scattergl(x=data_resids['Date'][::75],
                                           y=data_resids['W'][::75],
                                             name= 'W',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=1),
                                             showlegend=False),
                                             secondary_y=False, row=3, col=1)

    


# full_fig = fig.full_figure_for_development()
    
    if plot_num == 2 or plot_num == 0 or plot_num == 5:
        ###
        ### DENSITY AXIS
        fig.update_yaxes(title_text=r"$\text{Normal Residuals (m)}$", 
#                          type="log", 
#                          range=yaxis2_range, 
                         exponentformat= 'power',row=1, col=1)
        ###
        ### InTrack Residual Axis
        fig.update_yaxes( title=r"$\text{In-Track Residuals (m)}$",
#                          range=yaxis3_range, 
                         exponentformat= 'power',row=2, col=1)
        ###
        ### RMS AXIS
        fig.update_yaxes( title=r"$\text{Cross-Track Residuals (m)}$" ,
                         type="linear" ,
#                          range=yaxis4_range, 
                          exponentformat= 'power', row=3, col=1)
        ###
        ###  DATE on Final x-Axis only
        fig.update_xaxes(title=r"$\text{Date}$", 
                         range=[pd.to_datetime( "181108-160000", format='%y%m%d-%H%M%S'),
                                pd.to_datetime( "181124-120000", format='%y%m%d-%H%M%S')],
                         row=3, col=1)

        
    return(fig)

    
    
    
    
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------


    


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Plot 

In [24]:


fig = make_subplots(rows=3, cols=1,
#                     subplot_titles=([ ' ', ]),
                    #                     
                    specs=[[ {"secondary_y": False} ],
                           [ {"secondary_y": False} ],
                           [ {"secondary_y": False} ]],
                    #
                    vertical_spacing = 0.08,
                    shared_xaxes=True)




for model in run_dict.keys():
    fig = plot_NTWresids(fig, Obj_2weeks[model],  run_dict[model], solar_fluxes, arc_listlist)
  
    
#######################################################
font_dict=dict(family='Arial',size=16,color='black')
#######################################################

    

for i in [1,2,3]:
    fig.update_xaxes(### LINE at axis border
                      showline=True,
                      showticklabels=True,
                      linecolor='black',
                      linewidth=1,
                     ### Major ticks
                      ticks='inside',
                      tickfont=font_dict,
                      mirror=True,
                      tickwidth=2,
                      ticklen=9,
                      tickcolor='grey',
                      tick0="2018-11-9" ,
                      dtick=86400000.0*2,    # milliseconds in a day, every 7 days
                      #### Minor Ticks
                       minor=dict(
                         dtick=86400000.0, # milliseconds in a day
                         tickwidth=1,
                         ticklen=4,
                         tickcolor='grey',
                         ticks='inside'),
                      ### GRID
                       gridcolor='gainsboro',
                       gridwidth=1,
                       layer='above traces',
                       tickangle=0,
                       row=i, col=1)
    fig.update_yaxes(showline=True,      # add line at x=0
                         showticklabels=True,
                         linecolor='black',  # line color
                         linewidth=1,        # line size
                     ticks='inside',     # ticks outside axis
                     tickfont=font_dict, # tick label font
                     mirror='allticks',  # add ticks to top/right axes
                     tickwidth=1,      # tick width
                     tickcolor='black',  # tick color
                     gridcolor='gainsboro',
                     gridwidth=1,
                     layer='above traces',
                     row=i, col=1)


modelnames=[]
modelcolors = []
#### LEGEND ####
for model in run_dict.keys():
    if model == 'msis2':
        modelnames.append("MSISe2")
        modelcolors.append(col_msis2)

    elif model == 'dtm2020_o':
        modelnames.append("DTM2020")
        modelcolors.append(col_dtm2020)

    elif model == 'jb2008':
        modelnames.append("JB2008")
        modelcolors.append(col_jb2008)

    elif model == 'tiegcm_oc':
        modelnames.append("TIEGCM")
        modelcolors.append(col_tiegcm_oc)

    elif model == 'hasdm_oc':
        modelnames.append("HASDM")
        modelcolors.append(col_hasdm_oc)

    elif model == 'ctipe_oc':
        modelnames.append("CTIPe")
        modelcolors.append(col_ctipe_oc)



df = pd.DataFrame({"starts_colors": modelcolors
                                    })

fig.update_traces(showlegend=False).add_traces(
    [   go.Scattergl(name=modelnames[i], 
               x=[pd.to_datetime( "181107-000000", format='%y%m%d-%H%M%S')],
               mode='lines',
               line = dict(shape = 'hv',  width=10),
               marker_color=c, 
               showlegend=True)
        for i,c in enumerate((df.loc[:,["starts_colors"]].values.ravel()))])

fig.update_layout(legend=dict(
    yanchor="middle",
    y=0.5,
    xanchor="center",
    x=1.1,
#     x=1.015,
        font=font_dict      ,
        bgcolor="white",
        bordercolor="darkgrey",
        borderwidth=0.8,
    )  )

fig.update_layout(
#                   title = '',
                  autosize=False,    width=900,    height=850,
                  legend= {'itemsizing': 'trace'},
                  font=font_dict,
                  plot_bgcolor='white', 
                 )
fig.update_annotations(font_size=14)  # Increase size of subplot title

fig.show(#renderer="jpg",
         config=config)


    


##  RSW

In [9]:
# Obj_2weeks['msis2'].__dict__['Density']['2018.316.01']

In [10]:
%load_ext autoreload
%autoreload 2

# yaxis1_range = [-0.23888888888888893, 4.538888888888889] #full_fig.layout.yaxis1.range
# yaxis2_range = [-13.7,  -12.6]# -12.882954062508686] #full_fig.layout.yaxis2.range
# yaxis3_range = [-100, 60] #full_fig.layout.yaxis3.range
# yaxis4_range = [-2, 43] #full_fig.layout.yaxis4.range

def plot_RSWresids(fig, obj_m1, plot_num, solar_fluxes, arc_listlist ):
    

    ####  Get plot Parameters for this model
    model_m1 = obj_m1.__dict__['global_params']['den_model']
    col = get_plot_params(plot_num, model_m1)
    

    for i1,arc1 in enumerate(arc_listlist):#obj_m1.__dict__['global_params']['arc_input']):
        dateplot = []
        rms_totals = []
        
        for ii,arc in enumerate(arc1[3:4]):#obj_m1.__dict__['global_params']['arc_input']):
            if arc not in obj_m1.__dict__['global_params']['arc_input']:
                continue
            else:
                arc =arc+'.01'


                ### -----------------------------------------------------------------------------------------------------
                ###     Radial Orbit
                data_orbfil = obj_m1.__dict__['OrbitResids'][arc]['data_orbfil']
                data_pce = obj_m1.__dict__['OrbitResids'][arc]['data_PCE']
                
                fig.add_trace(go.Scattergl(x=data_pce['Date'],
                                           y=(np.array(data_pce['R'])*1e-3),
                                             name= 'Radial',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color='black',size=2),
                                                 line = dict( color = 'black', width=2),
                                             showlegend=False),
                                             secondary_y=False, row=1, col=1)
                fig.add_trace(go.Scattergl(x=data_orbfil['Date'],
                                           y=(np.array(data_orbfil['R'])*1e-3),
                                             name= 'Radial',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=2),
                                             showlegend=False),
                                             secondary_y=False, row=1, col=1)
                ### -----------------------------------------------------------------------------------------------------
                ###     Altitude Orbit
                fig.add_trace(go.Scattergl(x=obj_m1.__dict__['Density'][arc]['Date'][:],
                                           y=np.array(obj_m1.__dict__['Density'][arc]['Height (meters)'][:])*1e-3,
                                             name= 'Altitude',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=2),
                                             showlegend=False),
                                             secondary_y=False, row=2, col=1)
                ### -----------------------------------------------------------------------------------------------------
                ###     Radial Residuals
                data_resids = obj_m1.__dict__['OrbitResids'][arc]['resids']
                fig.add_trace(go.Scattergl(x=data_resids['Date'][::3],
                                           y=data_resids['R'][::3],
                                             name= 'Radial',
                                             mode='markers+lines',
                                             opacity=1,
                                                 marker=dict(color=col,size=2),
                                                 line = dict( color = col, width=2),
                                             showlegend=False),
                                             secondary_y=False, row=3, col=1)
                ### -----------------------------------------------------------------------------------------------------
                ###     Along Track Residuals
#                 data_resids = obj_m1.__dict__['OrbitResids'][arc]['resids']
#                 fig.add_trace(go.Scattergl(x=data_resids['Date'][::3],
#                                            y=data_resids['S'][::3],
#                                              name= 'Along track',
#                                              mode='markers+lines',
#                                              opacity=1,
#                                                  marker=dict(color=col,size=2),
#                                                  line = dict( color = col, width=3),
#                                              showlegend=False),
#                                              secondary_y=False, row=2, col=1)
#                 ### -----------------------------------------------------------------------------------------------------
#                 ###     Cross Track Residuals
#                 data_resids = obj_m1.__dict__['OrbitResids'][arc]['resids']
#                 fig.add_trace(go.Scattergl(x=data_resids['Date'][::3],
#                                            y=data_resids['Wrsw'][::3],
#                                              name= 'Wrsw',
#                                              mode='markers+lines',
#                                              opacity=1,
#                                                  marker=dict(color=col,size=2),
#                                                  line = dict( color = col, width=2),
#                                              showlegend=False),
#                                              secondary_y=False, row=3, col=1)




# full_fig = fig.full_figure_for_development()
    
    if plot_num == 2 or plot_num == 0 or plot_num == 5:
        ###
        ### DENSITY AXIS
        fig.update_yaxes(title_text=r"$\text{Radial Direction (km)}$", 
#                          type="log", 
#                          range=yaxis2_range, 
                         exponentformat= 'power',row=1, col=1)
        
        fig.update_yaxes(title_text=r"$\text{Altitude (km)}$", 
#                          type="log", 
#                          range=yaxis2_range, 
                         exponentformat= 'power',row=2, col=1)
        ###
        ### InTrack Residual Axis
        fig.update_yaxes( title=r"$\text{Radial Residual (PCE-Orbfil) (m)}$",
#                          range=yaxis3_range, 
                         exponentformat= 'power',row=3, col=1)
#         ###
#         ### RMS AXIS
#         fig.update_yaxes( title=r"$\text{Cross-Track Residuals (m)}$" ,
#                          type="linear" ,
# #                          range=yaxis4_range, 
#                           exponentformat= 'power', row=3, col=1)
        ###
        ###  DATE on Final x-Axis only
        fig.update_xaxes(title=r"$\text{Date}$", 
                         range=[pd.to_datetime( "181112-003000", format='%y%m%d-%H%M%S'),
                                pd.to_datetime( "181112-023000", format='%y%m%d-%H%M%S')],
                         row=3, col=1)

        
    return(fig)

    
    
    
    
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------
    ### -----------------------------------------------------------------------------------------------------


fig = make_subplots(rows=3, cols=1,
#                     subplot_titles=([ ' ', ]),
                    #                     
                    specs=[[ {"secondary_y": False} ],
                           [ {"secondary_y": False} ],
                           [ {"secondary_y": False} ],
                          ],
                    #
                    vertical_spacing = 0.08,
                    shared_xaxes=True)




for model in run_dict.keys():
    fig = plot_RSWresids(fig, Obj_2weeks[model],  run_dict[model], solar_fluxes, arc_listlist)
  
    
#######################################################
font_dict=dict(family='Arial',size=16,color='black')
#######################################################

    

for i in [1,2,3]:
    fig.update_xaxes(### LINE at axis border
                      showline=True,
                      showticklabels=True,
                      linecolor='black',
                      linewidth=1,
                     ### Major ticks
                      ticks='inside',
                      tickfont=font_dict,
                      mirror=True,
                      tickwidth=2,
                      ticklen=9,
                      tickcolor='grey',
#                       tick0="2018-11-9" ,
#                       dtick=86400000.0*2,    # milliseconds in a day, every 7 days
                      #### Minor Ticks
#                        minor=dict(
#                          dtick=86400000.0, # milliseconds in a day
#                          tickwidth=1,
#                          ticklen=4,
#                          tickcolor='grey',
#                          ticks='inside'),
                      ### GRID
                       gridcolor='gainsboro',
                       gridwidth=1,
                       layer='above traces',
                       tickangle=0,
                       row=i, col=1)
    fig.update_yaxes(showline=True,      # add line at x=0
                         showticklabels=True,
                         linecolor='black',  # line color
                         linewidth=1,        # line size
                     ticks='inside',     # ticks outside axis
                     tickfont=font_dict, # tick label font
                     mirror='allticks',  # add ticks to top/right axes
                     tickwidth=1,      # tick width
                     tickcolor='black',  # tick color
                     gridcolor='gainsboro',
                     gridwidth=1,
                     layer='above traces',
                     row=i, col=1)


modelnames=[]
modelcolors = []
#### LEGEND ####
for model in run_dict.keys():
    if model == 'msis2':
        modelnames.append("MSISe2")
        modelcolors.append(col_msis2)

    elif model == 'dtm2020_o':
        modelnames.append("DTM2020")
        modelcolors.append(col_dtm2020)

    elif model == 'jb2008':
        modelnames.append("JB2008")
        modelcolors.append(col_jb2008)

    elif model == 'tiegcm_oc':
        modelnames.append("TIEGCM")
        modelcolors.append(col_tiegcm_oc)

    elif model == 'hasdm_oc':
        modelnames.append("HASDM")
        modelcolors.append(col_hasdm_oc)

    elif model == 'ctipe_oc':
        modelnames.append("CTIPe")
        modelcolors.append(col_ctipe_oc)



# df = pd.DataFrame({"starts_colors": modelcolors
#                                     })

# fig.update_traces(showlegend=False).add_traces(
#     [   go.Scattergl(name=modelnames[i], 
#                x=[pd.to_datetime( "181107-000000", format='%y%m%d-%H%M%S')],
#                mode='lines',
#                line = dict(shape = 'hv',  width=10),
#                marker_color=c, 
#                showlegend=True)
#         for i,c in enumerate((df.loc[:,["starts_colors"]].values.ravel()))])

# fig.update_layout(legend=dict(
#     yanchor="middle",
#     y=0.5,
#     xanchor="center",
#     x=1.1,
# #     x=1.015,
#         font=font_dict      ,
#         bgcolor="white",
#         bordercolor="darkgrey",
#         borderwidth=0.8,
#     )  )

fig.update_layout(
#                   title = '',
                  autosize=False,    width=900,    height=850,
#                   autosize=True,
                  legend= {'itemsizing': 'trace'},
                  font=font_dict,
                  plot_bgcolor='white', 
                 )
fig.update_annotations(font_size=14)  # Increase size of subplot title

fig.show(#renderer="jpg",
         config=config)


    


    


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Plot